In [1]:
from collections import defaultdict
import sklearn
import tensorflow as tf
import numpy as np
def under_sample(inputs, labels, cap_val=60, shuffle=True):
    with tf.device("/cpu:0"):
        counter = defaultdict(int)
        indexes = sklearn.utils.shuffle(range(inputs.shape[0])) if shuffle else range(len(inputs))
        out_input = []
        out_label = []
        for ind in indexes:
            la = np.where(labels[ind] == 1)[0][0]
            counter[la] += 1
            if counter[la] <= cap_val:
                out_input.append(inputs[ind])
                out_label.append(labels[ind])
        del inputs, labels
        len_map = list(map(len, out_input))
        out_input = [im for d in out_input for im in d]
        return tf.RaggedTensor.from_row_lengths(
                    out_input,
                    row_lengths=len_map
                ), np.array(out_label)

2023-04-28 17:10:32.314762: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 AVX512F FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-04-28 17:10:41.069313: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /usr/local/cuda/extras/CUPTI/lib64:/usr/local/cuda/compat/lib:/usr/local/nvidia/lib:/usr/local/nvidia/lib64:/usr/local/cuda-11/lib64
2023-04-28 17:10:41.069485: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer_plugin.so.7'; dlerror: libnvinfer_plugin.so.7: cannot open shared object file: No such file or directory; LD_LIB

In [2]:
def split_ragged_tensor(x, y, val_fraction=0.2, seed=None):
    # compute the number of rows in the input tensors
    n_rows = x.shape[0]

    # compute the number of rows to use for validation
    n_val_rows = int(n_rows * val_fraction)

    # set the random seed for reproducibility
    if seed is not None:
        tf.random.set_seed(seed)

    # shuffle the rows of the tensors randomly
    shuffled_indices = tf.random.shuffle(tf.range(n_rows))
    x = tf.gather(x, shuffled_indices)
    y = tf.gather(y, shuffled_indices)

    # split the tensors into training and validation sets
    x_train = x[n_val_rows:, :]
    x_val = x[:n_val_rows, :]
    y_train = y[n_val_rows:]
    y_val = y[:n_val_rows]

    return x_train, x_val, y_train, y_val

In [3]:
def smooth_labels(labels, factor=0.1):
        # smooth the labels
        labels *= (1 - factor)
        labels += (factor / labels.shape[1])
        # returned the smoothed labels
        return labels

In [4]:
import joblib

x = joblib.load("data_x_1D.p")
y = joblib.load("data_y_1D.p")

print(x.shape)
print(y.shape)

(2583, None, 175, 1)
(2583, 27)


2023-04-28 17:10:48.190179: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcufft.so.10'; dlerror: libcufft.so.10: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /usr/local/cuda/extras/CUPTI/lib64:/usr/local/cuda/compat/lib:/usr/local/nvidia/lib:/usr/local/nvidia/lib64:/usr/local/cuda-11/lib64
2023-04-28 17:10:48.220838: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcusparse.so.11'; dlerror: libcusparse.so.11: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /usr/local/cuda/extras/CUPTI/lib64:/usr/local/cuda/compat/lib:/usr/local/nvidia/lib:/usr/local/nvidia/lib64:/usr/local/cuda-11/lib64
2023-04-28 17:10:48.221092: W tensorflow/core/common_runtime/gpu/gpu_device.cc:1934] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are installed properly if you would like to 

In [5]:
x, y = under_sample(x, y)
x_train, x_test, y_train, y_test = split_ragged_tensor(x,
                                                       y,
                                                       val_fraction=0.2,
                                                       seed=42)
x_train, x_valid, y_train, y_valid = split_ragged_tensor(x_train,
                                                         y_train,
                                                         val_fraction=0.2,
                                                         seed=42)

In [6]:
y_train = smooth_labels(y_train)

In [7]:
# max allowed timesteps is 200
x_train = (x_train).to_tensor(default_value=-1.0, shape=[None, 200, 175, 1])[..., 0]
x_valid = (x_valid).to_tensor(default_value=-1.0, shape=[None, 200, 175, 1])[..., 0]
x_test = (x_test).to_tensor(default_value=-1.0, shape=[None, 200, 175, 1])[..., 0]

In [8]:
print(x_train.shape, x_valid.shape, x_test.shape)

(858, 200, 175) (214, 200, 175) (267, 200, 175)


In [9]:
def representative_dataset_gen():
    for i in x_test:
        yield [i]

In [10]:
import tensorflow as tf

omodel = tf.keras.models.load_model(r"models/lstm128_attention_epoch300_dense64_drop1_bnorm1.h5")
model_conf = omodel.get_config()
model_conf["layers"][0]["config"]["batch_input_shape"] = (None, 200, 175)
model = tf.keras.Model.from_config(model_conf)

for new_layer, layer in zip(model.layers[1:], omodel.layers[1:]):
    new_layer.set_weights(layer.get_weights())

model.compile(loss="categorical_crossentropy", metrics=["acc"])

model.evaluate(x_test, y_test)
model.summary()

model.save("model.h5")

9/9 [==============================] - 2s 38ms/step - loss: 0.4490 - acc: 0.9251
Model: "model_15"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_17 (InputLayer)          [(None, 200, 175)]   0           []                               
                                                                                                  
 masking_16 (Masking)           (None, 200, 175)     0           ['input_17[0][0]']               
                                                                                                  
 lstm_16 (LSTM)                 (None, 200, 128)     155648      ['masking_16[0][0]']             
                                                                                                  
 attention_16 (Attention)       (None, 200, 128)     0           ['lstm_16[0][0]',                
          

In [11]:
from tensorflow import keras
class Distiller(keras.Model):
    def __init__(self, student, teacher):
        super().__init__()
        self.teacher = teacher
        self.student = student

    def compile(
        self,
        optimizer,
        metrics,
        student_loss_fn,
        distillation_loss_fn,
        alpha=0.1,
        temperature=3,
    ):
        """ Configure the distiller.

        Args:
            optimizer: Keras optimizer for the student weights
            metrics: Keras metrics for evaluation
            student_loss_fn: Loss function of difference between student
                predictions and ground-truth
            distillation_loss_fn: Loss function of difference between soft
                student predictions and soft teacher predictions
            alpha: weight to student_loss_fn and 1-alpha to distillation_loss_fn
            temperature: Temperature for softening probability distributions.
                Larger temperature gives softer distributions.
        """
        super().compile(optimizer=optimizer, metrics=metrics)
        self.student_loss_fn = student_loss_fn
        self.distillation_loss_fn = distillation_loss_fn
        self.alpha = alpha
        self.temperature = temperature

    def train_step(self, data):
        # Unpack data
        x, y = data

        # Forward pass of teacher
        teacher_predictions = self.teacher(x, training=False)

        with tf.GradientTape() as tape:
            # Forward pass of student
            student_predictions = self.student(x, training=True)

            # Compute losses
            student_loss = self.student_loss_fn(y, student_predictions)

            # Compute scaled distillation loss from https://arxiv.org/abs/1503.02531
            # The magnitudes of the gradients produced by the soft targets scale
            # as 1/T^2, multiply them by T^2 when using both hard and soft targets.
            distillation_loss = (
                self.distillation_loss_fn(
                    tf.nn.softmax(teacher_predictions / self.temperature, axis=1),
                    tf.nn.softmax(student_predictions / self.temperature, axis=1),
                )
                * self.temperature**2
            )

            loss = self.alpha * student_loss + (1 - self.alpha) * distillation_loss

        # Compute gradients
        # trainable_vars = self.student.trainable_variables
        # gradients = tape.gradient(loss, trainable_vars)
        gradients = tape.gradient(loss, self.student.trainable_variables)

        # Update weights
        # self.optimizer.apply_gradients(zip(gradients, trainable_vars))
        self.optimizer.apply_gradients(zip(gradients, self.student.trainable_variables))

        # Update the metrics configured in `compile()`.
        self.compiled_metrics.update_state(y, student_predictions)

        # Return a dict of performance
        results = {m.name: m.result() for m in self.metrics}
        results.update(
            {"student_loss": student_loss, "distillation_loss": distillation_loss}
        )
        return results

    def test_step(self, data):
        # Unpack the data
        x, y = data

        # Compute predictions
        y_prediction = self.student(x, training=False)

        # Calculate the loss
        student_loss = self.student_loss_fn(y, y_prediction)

        # Update the metrics.
        self.compiled_metrics.update_state(y, y_prediction)

        # Return a dict of performance
        results = {m.name: m.result() for m in self.metrics}
        results.update({"student_loss": student_loss})
        return results

    def get_student_model(self):
        y_pred = self.student(x_test, training=False)
        acc = (np.argmax(y_pred) == np.argmax(y_test)).mean()
        print(acc)
        
        trained_student_model = tf.keras.models.clone_model(self.student)
        trained_student_model.set_weights(self.student.get_weights())
        return trained_student_model

In [12]:
from tensorflow.keras.layers import Input, LSTM, Dense, Dropout, Masking, BatchNormalization, GlobalAveragePooling1D
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Attention

def create_student_model(lstm_units=108):
    # Define input shape
    input_shape = (200, 175)
    # lstm_units = 108
    max_len = 100
    d_emb = 175

    # Define model architecture
    inputs = Input(shape=input_shape)
    mask_layer = Masking(mask_value=-1.0)(inputs)
    lstm_outputs = LSTM(units=lstm_units, return_sequences=True, kernel_regularizer="l2")(mask_layer)

    attention_outputs = Attention()([lstm_outputs, lstm_outputs])
    batch_norm_outputs = BatchNormalization(momentum=0.1)(attention_outputs)
    pooled_outputs = GlobalAveragePooling1D()(batch_norm_outputs)
    dense_outputs = Dense(units=64, activation='relu')(pooled_outputs)
    dense_outputs = Dropout(0.4)(dense_outputs)
    dense_outputs = Dense(units=27, activation='softmax')(dense_outputs)

    # Build and compile model
    student_model = Model(inputs=inputs, outputs=dense_outputs)

    # Print model summary
    student_model.summary()
    return student_model

In [23]:
student_model = create_student_model(lstm_units=88)
student_model.compile(loss=keras.losses.CategoricalCrossentropy(), 
                      metrics=[keras.metrics.CategoricalAccuracy()]
                     )
distiller = Distiller(student=student_model, teacher=model)
distiller.compile(
    optimizer=keras.optimizers.Adam(learning_rate=0.0005),
    metrics=[keras.metrics.CategoricalAccuracy()],
    student_loss_fn=keras.losses.CategoricalCrossentropy(from_logits=True),
    distillation_loss_fn=keras.losses.KLDivergence(),
    alpha=0.1,
    temperature=6,
)

# Distill teacher to student
distiller.fit(x_train, y_train, epochs=250)

# Evaluate student on test dataset
acc_loss = distiller.evaluate(x_test, y_test)
print(acc_loss)

student_model.evaluate(x_test, y_test)

Model: "model_4"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_5 (InputLayer)           [(None, 200, 175)]   0           []                               
                                                                                                  
 masking_4 (Masking)            (None, 200, 175)     0           ['input_5[0][0]']                
                                                                                                  
 lstm_4 (LSTM)                  (None, 200, 88)      92928       ['masking_4[0][0]']              
                                                                                                  
 attention_4 (Attention)        (None, 200, 88)      0           ['lstm_4[0][0]',                 
                                                                  'lstm_4[0][0]']           

27/27 [==============================] - 3s 101ms/step - categorical_accuracy: 0.5093 - student_loss: 1.9153 - distillation_loss: 0.0077
Epoch 38/250
27/27 [==============================] - 3s 101ms/step - categorical_accuracy: 0.5455 - student_loss: 1.8720 - distillation_loss: 0.0074
Epoch 39/250
27/27 [==============================] - 3s 101ms/step - categorical_accuracy: 0.5361 - student_loss: 1.8680 - distillation_loss: 0.0073
Epoch 40/250
27/27 [==============================] - 3s 102ms/step - categorical_accuracy: 0.5723 - student_loss: 1.8051 - distillation_loss: 0.0069
Epoch 41/250
27/27 [==============================] - 3s 101ms/step - categorical_accuracy: 0.5734 - student_loss: 1.7895 - distillation_loss: 0.0071
Epoch 42/250
27/27 [==============================] - 3s 101ms/step - categorical_accuracy: 0.6037 - student_loss: 1.7647 - distillation_loss: 0.0068
Epoch 43/250
27/27 [==============================] - 3s 100ms/step - categorical_accuracy: 0.5886 - student_loss

27/27 [==============================] - 3s 100ms/step - categorical_accuracy: 0.7448 - student_loss: 1.4214 - distillation_loss: 0.0045
Epoch 92/250
27/27 [==============================] - 3s 100ms/step - categorical_accuracy: 0.7599 - student_loss: 1.3904 - distillation_loss: 0.0043
Epoch 93/250
27/27 [==============================] - 3s 101ms/step - categorical_accuracy: 0.7587 - student_loss: 1.4158 - distillation_loss: 0.0045
Epoch 94/250
27/27 [==============================] - 3s 100ms/step - categorical_accuracy: 0.7261 - student_loss: 1.4383 - distillation_loss: 0.0047
Epoch 95/250
27/27 [==============================] - 3s 100ms/step - categorical_accuracy: 0.7786 - student_loss: 1.3654 - distillation_loss: 0.0043
Epoch 96/250
27/27 [==============================] - 3s 101ms/step - categorical_accuracy: 0.7692 - student_loss: 1.4188 - distillation_loss: 0.0045
Epoch 97/250
27/27 [==============================] - 3s 100ms/step - categorical_accuracy: 0.7587 - student_loss

27/27 [==============================] - 3s 101ms/step - categorical_accuracy: 0.8322 - student_loss: 1.2754 - distillation_loss: 0.0035
Epoch 146/250
27/27 [==============================] - 3s 101ms/step - categorical_accuracy: 0.8392 - student_loss: 1.2464 - distillation_loss: 0.0034
Epoch 147/250
27/27 [==============================] - 3s 100ms/step - categorical_accuracy: 0.8310 - student_loss: 1.2776 - distillation_loss: 0.0035
Epoch 148/250
27/27 [==============================] - 3s 100ms/step - categorical_accuracy: 0.8508 - student_loss: 1.2736 - distillation_loss: 0.0034
Epoch 149/250
27/27 [==============================] - 3s 100ms/step - categorical_accuracy: 0.8392 - student_loss: 1.2484 - distillation_loss: 0.0035
Epoch 150/250
27/27 [==============================] - 3s 101ms/step - categorical_accuracy: 0.8287 - student_loss: 1.2802 - distillation_loss: 0.0035
Epoch 151/250
27/27 [==============================] - 3s 101ms/step - categorical_accuracy: 0.8240 - studen

27/27 [==============================] - 3s 101ms/step - categorical_accuracy: 0.8648 - student_loss: 1.2033 - distillation_loss: 0.0030
Epoch 200/250
27/27 [==============================] - 3s 100ms/step - categorical_accuracy: 0.8578 - student_loss: 1.1932 - distillation_loss: 0.0029
Epoch 201/250
27/27 [==============================] - 3s 101ms/step - categorical_accuracy: 0.8753 - student_loss: 1.1740 - distillation_loss: 0.0027
Epoch 202/250
27/27 [==============================] - 3s 101ms/step - categorical_accuracy: 0.8765 - student_loss: 1.1631 - distillation_loss: 0.0029
Epoch 203/250
27/27 [==============================] - 3s 100ms/step - categorical_accuracy: 0.8683 - student_loss: 1.1765 - distillation_loss: 0.0028
Epoch 204/250
27/27 [==============================] - 3s 101ms/step - categorical_accuracy: 0.8741 - student_loss: 1.1640 - distillation_loss: 0.0027
Epoch 205/250
27/27 [==============================] - 3s 101ms/step - categorical_accuracy: 0.8706 - studen

[4.226631164550781, 0.8764045238494873]

In [24]:
student_model.save("distilled_model_88.h5")

In [27]:
st = keras.models.load_model("distilled_model.h5")

In [28]:
st.compile(metrics=["acc"], loss="categorical_crossentropy")
st.evaluate(x_valid, y_valid)

7/7 [==============================] - 2s 29ms/step - loss: 4.0618 - acc: 0.8598


[4.061826229095459, 0.8598130941390991]

In [29]:
st.summary()

Model: "model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_1 (InputLayer)           [(None, 200, 175)]   0           []                               
                                                                                                  
 masking (Masking)              (None, 200, 175)     0           ['input_1[0][0]']                
                                                                                                  
 lstm (LSTM)                    (None, 200, 84)      87360       ['masking[0][0]']                
                                                                                                  
 attention (Attention)          (None, 200, 84)      0           ['lstm[0][0]',                   
                                                                  'lstm[0][0]']               